In [ ]:
import os
import pandas as pd
from sklearn.linear_model import LinearRegression
from sklearn.neighbors import KNeighborsRegressor,RadiusNeighborsRegressor
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import PolynomialFeatures
from sklearn.tree import DecisionTreeRegressor

algs = {
    'canter': 'KNeighbors-6-distance',
    'josh': 'polynomial-4'
}

results = pd.DataFrame({'force':range(1,65535)})
actual = {}
pX = results['force'].to_numpy().reshape(-1,1)
for k,v in algs.items():
    #read in data
    parts = v.split('-')
    df = pd.read_csv(f'data/{k}-clean.csv')

    #set up ML inputs
    X = df['force'].to_numpy().reshape(-1, 1)
    Y = df['rpm'].to_numpy()

    #run selected algorithm
    if parts[0] == 'DecisionTree':
        dt = DecisionTreeRegressor(max_depth=int(parts[1]))
        pY = dt.fit(X,Y).predict(pX)
    elif parts[0] == 'KNeighbors':
        knn = KNeighborsRegressor(int(parts[1]), weights=parts[2])
        pY = knn.fit(X,Y).predict(pX)
    elif parts[0] == 'RNeighbors':
        rnn = RadiusNeighborsRegressor(int(parts[1]), weights=parts[2])
        pY = rnn.fit(X,Y).predict(pX)
    else:
        polynomial_features = PolynomialFeatures(degree=int(parts[1]), include_bias=False)
        linear_regression = LinearRegression()
        pipeline = Pipeline(
            [
                ("polynomial_features", polynomial_features),
                ("linear_regression", linear_regression),
            ]
        )
        pY = pipeline.fit(X,Y).predict(pX)
    results[k] = pd.Series(pY)
    actual[k] = df
results

In [ ]:
import plotly.graph_objects as go

fig = go.Figure()

for name in results.columns[1:]:
    fig.add_trace(
        go.Scatter(
            name=name,
            x=results.force,
            y=results[name]
        )
    )
    fig.add_trace(
        go.Scatter(
            name=f'{name}-actual',
            x=actual[name].force,
            y=actual[name].rpm,
            mode='markers'
        )
    )
fig